## 120 Quartics 

In [ ]:
using HomotopyContinuation
using MultivariatePolynomials

We need the function var_coefficients(f,t) to compute the coefficients of a polynomial f with respect to a variable t.

In [2]:
#return the t^m-coefficient of f, where t is a variable
function var_coeff(f,t,m)
    v = terms(f)
    v = filter(a -> (degree(a,t) == m),v)
    if length(v) == 0
        return polynomial(zeroterm(t))
    end
    v = map(a -> div(a,1.0*t^m),v)
    v = map(a -> subs(a,t => 0),v)
    return reduce(+,v)
end 

function var_coefficients(f,t)
    d = maxdegree(f,t)
    v = Array{AbstractPolynomial}(undef,d+1) 
    for m=0:d
        v[d-m+1] = polynomial(var_coeff(f,t,m))
    end
    return v 
end

var_coefficients (generic function with 1 method)

We take f to be a quartic in normal form and choose f_2, f_3 as quite generic degree 4 and 6 binary forms.

In [3]:
@polyvar z x y  c[0:14] d[0:14] 

f = c[1]*x^4 + c[3]*x^3*z + c[4]*x^2*y^2 + c[5]*x^2*y*z + c[6]*x^2*z^2 + c[7]*x*y^3 + c[8]*x*y^2*z + c[9]*x*y*z^2  +  c[11]*y^4 + c[12]*y^3*z + c[13]*y^2*z^2 + c[15]*y*z^3 + c[15]*z^4
p = var_coefficients(f,z)

#use equation (4) on page 18 in Vakils paper
u_2 = p[2]*p[4] - 4p[1]*p[5] - p[3]^2/3
u_3 = p[2]^2*p[5] + p[1]*p[4]^2 - 8p[1]*p[3]*p[5]/3 - p[2]*p[3]*p[4]/3  +2p[3]^3/27


f_2 = x^4 + 3x^3*y + 5x^2*y^2 + 7x*y^3 + 9y^4
f_3 = x^6 + 2*x^5*y + 3*x^4*y^2 + 4*x^3*y^3 + 5*x^2*y^4 + 6*x*y^5 + 7*y^6

x⁶ + 2x⁵y + 3x⁴y² + 4x³y³ + 5x²y⁴ + 6xy⁵ + 7y⁶

By demanding the vanishing of the coefficients of u_2 - f_2 and u_3 - f_3 t, we get twelve nonhomogenous equations. HomotopyContinuation.jl solves them for us.

In [4]:
h_2 = u_2 - f_2
h_3 = u_3 - f_3
h_2 = subs(h_2,y =>1)
h_3 = subs(h_3,y => 1)

v = var_coefficients(h_2,x)
w = var_coefficients(h_3,x)

s = [v[i] for i in 1:length(v)]
for i in 1:length(w)
    push!(s,w[i])
end

F = System(s)
res = solve(F)
sol = solutions(res)

Tracking 234 paths... 100%|█████████████████████████████| Time: 0:00:11
  # paths tracked:                  234
  # non-singular solutions (real):  120 (8)
  # singular endpoints (real):      0 (0)
  # total solutions (real):         120 (8)


120-element Vector{Vector{ComplexF64}}:
 [-0.002999182663836804 - 0.0018445841878379794im, 0.042014686306177974 + 0.00897059872046452im, -0.016009209477069186 - 0.007554261312818278im, -0.1894506360380634 - 0.33538044581026777im, -0.5255017569540404 - 1.7113528455970557im, -0.029062075894411267 - 0.0348758805051172im, -0.2753224500274953 - 0.5547102977368354im, -0.7803152195997181 - 2.0411622811052097im, 0.025249342981252504 - 0.07460826327778351im, 1.324497959351418 - 0.356643966691034im, 10.667010079914279 + 5.257505371723499im, 29.304932613839156 + 31.952396126211465im]
 [0.04012458761118343 - 3.17310994922088e-68im, -0.9202090454184744 + 4.8683330727772406e-67im, -0.10043779038739781 + 6.3172417253895145e-68im, -1.008452251547852 + 2.3414363826214347e-67im, 6.131870050056369 - 1.557866583288717e-66im, 0.10862384872649553 - 5.955014562236446e-68im, 2.6393289446986654 - 6.166555225517838e-67im, 18.247046914454984 + 7.0474916863061e-67im, -0.033768574321275 + 1.4996204554537036e-68im,